# Interactive Viz

First, we import the packages that we will need.

In [2]:
import numpy as np
import json
from pprint import pprint
import pandas as pd
from bs4 import BeautifulSoup
import requests
import folium

To get the location of each university/institution (in which canton it belongs to), we decided to use Geonames.org in the same way as the previous homework. We used requests and then BeautifulSoup.

In [3]:
url = 'http://www.geonames.org/search.html?'
param = {'q' : '', 'country':'CH'}

data = {}

#We open the json file
with open('ch-cantons.topojson.json') as data_file:    
    data = json.load(data_file)

#We import the data and clear it, deleting the NaN and selecting the features that we need
GrantExport = pd.read_csv("P3_GrantExport.csv",sep=';')
GrantExport = GrantExport[['Institution','University','Approved Amount']]
GrantExport.dropna(subset=['Approved Amount'], inplace=True)
GrantExport.dropna(subset=['Institution','University'], how='all', inplace=True)
GrantExport = GrantExport.ix[~(GrantExport['University'] == 'Nicht zuteilbar - NA')]
GrantExport = GrantExport.ix[~(GrantExport['Approved Amount'] == 'data not included in P3')]
GrantExport['Approved Amount']=GrantExport['Approved Amount'].astype(float)
GrantExport.fillna(value='NO_INFORMATION',inplace=True) #So, we can delete by doing a groupby
GrantExport = GrantExport.ix[~(GrantExport['University'] == 'NO_INFORMATION')]


#We remove the hautes écoles spécialisées because they belongs to 5 different cantons
GrantExport = GrantExport.ix[~(GrantExport['University'] == 'HES de Suisse occidentale - HES-SO')]

#We remove those ones too because several universities work on those projects
GrantExport = GrantExport.ix[~(GrantExport['University'] == 'Swiss Institute of Bioinformatics - SIB')]

GrantExport = GrantExport.ix[~(GrantExport['University'] == 'Forschungskommission SAGW')]

In [4]:
GrantExport_final = GrantExport.groupby(['University', 'Institution']).sum().reset_index()
GrantExport_final = GrantExport_final.set_index(['University'])

We create an array that contains the names of the cantons. This array will help us to assign each university/institution to the corresponding canton. Moreover, we add other versions of the same canton as Zürcher which is the German name of Zurich same for Tessin and we add vaud too because the capital letter doesn't appear automatically in our data. 

In [5]:
cantons = []

for canton in data['objects']['cantons']['geometries'] : 
    cantons.append(canton['properties']['name'])

#There are special characters, we modify them

spec_char = {'Ã¼':'ü','Ã¢':'â','Ã¨':'è', 'Ã¼' : 'ü'}

for index , canton in enumerate(cantons) :    
    
        if('/' in canton) :
            name1 , name2 = canton.split('/')
            cantons[index] = name1
            cantons.append(name2)
            
        for char in spec_char.keys() : 
            if(char in cantons[index]) : 
                cantons[index] = cantons[index].replace(char,spec_char[char])
                
cantons.append('Zürcher')
cantons.append('vaud')
cantons.append('Tessin')

We create a dataframe 'FINAL' that will contain the final results used for the map, and an other dataframe 'Frame_For_Institutions' that stores the data according to the institution and not the university because the university feature doesn't contain any information about the location (ex: NPO - Not Profitable Organisation). 

In [6]:
FINAL = pd.DataFrame(columns=['Canton', 'Approved Amount'])
Frame_For_Insitutions = GrantExport_final.loc['NPO (Biblioth., Museen, Verwalt.) - NPO']
GrantExport_final = GrantExport_final.ix[~(GrantExport_final.index == 'NPO (Biblioth., Museen, Verwalt.) - NPO')]

We go through the dataframe GrantExport_final that contains all the data. The index is the name of the University to avoid redundant requests. Moreover, to avoid useless requests, we check if the name of the canton appears in the name of the university (ex : Université de Genève, Université de Neuchatel etc...). If it doesn't appear, we use the API geonames.org to try to find the corresponding canton, first by using the name of the university (ex : Université de Lausanne) and if we have no results, we use the code (ex : EPF Lausanne doesn't work but EPFL does). If both don't work, we append the corresponding project to the Dataframe 'Frame_for_institutions' that we will use later to try to find the canton using the field 'Institution'.

In [7]:
for index in GrantExport_final.index.drop_duplicates() : 
    
    temp_frame = GrantExport_final.loc[index]   
    stop = False
    
    tab = str(index).split('-') #Get the university and its code
    university = ''.join(tab[0:-1])
    code = tab[-1]
    
      
    #The ones that we add manually 
    
    if(index=='Paul Scherrer Institut - PSI') :
        dic = {'Canton' : 'Aargau', 'Approved Amount' : temp_frame['Approved Amount'].sum()}
        FINAL = FINAL.append(pd.Series(dic), ignore_index=True)
        GrantExport_final.drop(index, inplace=True)
        continue
        
    if(index=='Friedrich Miescher Institute - FMI') :
        dic = {'Canton' : 'Basel-Stadt', 'Approved Amount' : temp_frame['Approved Amount'].sum()}
        FINAL = FINAL.append(pd.Series(dic), ignore_index=True)
        GrantExport_final.drop(index, inplace=True)
        continue
        
    if(index=='Institut Universitaire Kurt Bösch - IUKB') :
        dic = {'Canton' : 'Valais', 'Approved Amount' : temp_frame['Approved Amount'].sum()}
        FINAL = FINAL.append(pd.Series(dic), ignore_index=True)
        GrantExport_final.drop(index, inplace=True)
        continue  
        
    
    #Look if the name appears the index
    for canton in cantons : 
        
        if canton in str(index) :  

            dic = {'Canton' : canton , 'Approved Amount' : temp_frame['Approved Amount'].sum()}
            FINAL = FINAL.append(pd.Series(dic), ignore_index=True)
            GrantExport_final.drop(index, inplace=True)

            stop = True
            break    
    
    
    if(stop == True) : 
        continue   
        
    #If the name does not appear in the index
    
    param['q'] = university
    r = requests.get(url, params=param)
    soup = BeautifulSoup(r.content,"lxml")
        
    if('We have found no places with the name' not in soup.prettify()) :   #TOUT EST OK ON TROUVE DES RESULTATS
             
            for canton in cantons : 
                
                if (canton in str(soup.findAll())) :
                    dic = {'Canton' : canton , 'Approved Amount' : float(temp_frame['Approved Amount'].sum())}
                    FINAL = FINAL.append(pd.Series(dic), ignore_index=True)
                    GrantExport_final.drop(index, inplace=True)
                    break
                        
    else :  #final case
            
        param['q'] = code
        r = requests.get(url, params=param)
        soup = BeautifulSoup(r.content,"lxml")
            
        if('We have found no places with the name' in soup.prettify()) :
                
            Frame_For_Insitutions = pd.concat([Frame_For_Insitutions,temp_frame])

            
        else :  #If we found a code we add it
            
            for canton in cantons : 
                
                if (canton in str(soup.findAll())) :
                    dic = {'Canton' : canton , 'Approved Amount' : float(temp_frame['Approved Amount'].sum())}
                    FINAL = FINAL.append(pd.Series(dic), ignore_index=True)
                    GrantExport_final.drop(index, inplace=True)
                    break                   
  

/Users/selmachraibi/anaconda/lib/python3.5/site-packages/pandas/indexes/api.py:71: RuntimeWarning: unorderable types: str() < int(), sort order is undefined for incomparable objects
  result = result.union(other)
/Users/selmachraibi/anaconda/lib/python3.5/site-packages/pandas/indexes/api.py:71: RuntimeWarning: unorderable types: int() > str(), sort order is undefined for incomparable objects
  result = result.union(other)


We use the same process as above for 'Frame_for_Insitutions'

In [8]:
Frame_For_Insitutions = Frame_For_Insitutions.reset_index()[['Institution','Approved Amount']].dropna()
 

for index in Frame_For_Insitutions.index :
    
    row = Frame_For_Insitutions.loc[index]
    institution = str(row['Institution'])
    stop = False
    
    
    #Case where the name of the cantons appears in the name of the institution
        
    for canton in cantons : 
        
        if canton in str(row['Institution']) :  
            
            dic = {'Canton' : canton , 'Approved Amount' : float(row['Approved Amount'])}
            FINAL = FINAL.append(pd.Series(dic), ignore_index=True)
            Frame_For_Insitutions.drop(index, inplace=True)
            stop = True
            break
            
            
    if(stop == True) : 
        continue   
         
        
       
    param['q'] = institution
    r = requests.get(url, params=param)
    soup = BeautifulSoup(r.content,"lxml")  
        
    #Case where the institution gives us no additional information
        
    if('We have found no places with the name' in str(soup.findAll())) :
        Frame_For_Insitutions.drop(index, inplace=True)
        continue
          
    #if we get the information from the institution, we look for it in the "soup"
    elif('no records found in geonames database, showing wikipedia results' not in soup.prettify()) : 
              
        for canton in cantons : 
                
            if (canton in str(soup.findAll())) :
                dic = {'Canton' : canton , 'Approved Amount' : float(row['Approved Amount'])}
                FINAL = FINAL.append(pd.Series(dic), ignore_index=True)

                Frame_For_Insitutions.drop(index, inplace=True)
                break


Universities for which we didn't find the corresponding canton. We prefered to delete them from the final dataframe because the API didn't work well.

In [9]:
Frame_For_Insitutions

Institution  Approved Amount
17                                       Antikenmuseum         977384.0
32                                 Archäologie Schweiz          68200.0
59              Bibliothèque publique et universitaire          37250.0
65                      Bundesamt für Landestopografie         590000.0
76                                    Burgerbibliothek          15000.0
97                       Collège Cantonal Saint-Michel          20695.0
104                          Conservatoire de Lausanne           9760.0
154                            Fondation Martin Bodmer           4000.0
164  Foundation for Research on Information Technol...          10000.0
168                                                GGG         210000.0
172    Gesellschaft für Schweizerische Kunstgeschichte        5387806.0
180                   Historisches Lexikon der Schweiz           2150.0
204                          Jacob Burckhardt-Stiftung        2568156.0
208                            Kantonale Denkmalpflege        3429745.0
212                                 Kantonsarchäologie          16280.0
227                          Kantonsschule Stadelhofen          36948.0
268                                        MeteoSuisse         592736.0
273                                 Museo di Valmaggia         284784.0
281                       Musée Historique de Lausanne          17280.0
282                   Musée International d'Horlogerie         463774.0
283         Musée cantonal d'archéologie et d'histoire         271172.8
286                 Musée de zoologie Palais de Rumine          80000.0
304                       Office féderal de la justice          15000.0
318                                   Rätisches Museum         408128.0
319                         Römerstadt Augusta Raurica        1745980.0
374                                       Staatsarchiv         455364.0
387                                       Stiftsarchiv          42500.0
393                     Stiftung Kinderdorf Pestalozzi         256000.0
402                                      Sucht Schweiz        1144924.0
410                                   Tribunal fédéral          59306.0
428                                  Vindonissa Museum         136047.0
435                                 Webster University           3000.0
450  École des Hautes Études Commerciales Universit...         349500.0
560  Foundation for Research on Information Technol...         705370.0
573                        Health Management Institute         216692.0
621                                Novartis Pharma Ltd         573934.0

We need to replace the name of the cantons to correspond to the names given in the json file.

In [10]:
FINAL.replace(to_replace='Tessin',value='Ticino', inplace=True)
FINAL.replace(to_replace='Zürcher',value='Zürich', inplace=True)
FINAL.replace(to_replace='Valais',value='Valais/Wallis', inplace=True)
FINAL.replace(to_replace='Wallis',value='Valais/Wallis', inplace=True)
FINAL.replace(to_replace='vaud',value='Vaud', inplace=True)
FINAL.replace(to_replace='Bern', value='Bern/Berne', inplace=True)
FINAL.replace(to_replace='Graubünden', value='Graubünden/Grigioni', inplace=True)

Finally, we group by the cantons and sum the results in order to have a final dataframe with the approved amount for each canton.

In [11]:
FINAL_ = FINAL.groupby('Canton').sum()
Finale = FINAL_.reset_index()
Finale['Approved Amount'] = Finale['Approved Amount']/(10**6)
Finale

Canton  Approved Amount
0                Aargau       121.894568
1      Basel-Landschaft        43.754286
2           Basel-Stadt      1393.492140
3            Bern/Berne      1579.776782
4              Fribourg       460.282105
5                Genève      1848.870374
6   Graubünden/Grigioni         3.493744
7                Luzern        54.154978
8             Neuchâtel       385.451750
9             Nidwalden         1.456715
10             Obwalden         0.138096
11         Schaffhausen         1.117484
12               Schwyz         1.483911
13            Solothurn         1.354401
14           St. Gallen        93.248968
15              Thurgau         6.119260
16               Ticino       112.075035
17                  Uri         0.105000
18        Valais/Wallis       214.984365
19                 Vaud      2361.049029
20                  Zug         0.868915
21               Zürich      3539.080561

We found only 22 cantons over 26. So, we add the missing cantons with null value.

In [12]:
missing_cantons = pd.DataFrame([['Appenzell Ausserrhoden', 0.0],['Appenzell Innerrhoden',0.0],
                             ['Glarus',0.0],['Jura', 0.0]],
                            columns=['Canton','Approved Amount'])
Finale = Finale.append(missing_cantons, ignore_index=True)
Finale

Canton  Approved Amount
0                   Aargau       121.894568
1         Basel-Landschaft        43.754286
2              Basel-Stadt      1393.492140
3               Bern/Berne      1579.776782
4                 Fribourg       460.282105
5                   Genève      1848.870374
6      Graubünden/Grigioni         3.493744
7                   Luzern        54.154978
8                Neuchâtel       385.451750
9                Nidwalden         1.456715
10                Obwalden         0.138096
11            Schaffhausen         1.117484
12                  Schwyz         1.483911
13               Solothurn         1.354401
14              St. Gallen        93.248968
15                 Thurgau         6.119260
16                  Ticino       112.075035
17                     Uri         0.105000
18           Valais/Wallis       214.984365
19                    Vaud      2361.049029
20                     Zug         0.868915
21                  Zürich      3539.080561
22  Appenzell Ausserrhoden         0.000000
23   Appenzell Innerrhoden         0.000000
24                  Glarus         0.000000
25                    Jura         0.000000

The amounts are given in Millions of CHF.
For the threshold scale, we tried to choose one that represents well the differences between the cantons.

In [17]:
canton_topo = r'ch-cantons.topojson.json'


# Let Folium determine the scale.
m = folium.Map(location=[46.5, 8], zoom_start=7)

m.choropleth(geo_path=canton_topo,
            data=Finale,
            columns=['Canton', 'Approved Amount'],
        
            key_on='feature.properties.name',
            threshold_scale=[0,1, 100, 500, 1500, 2000],
            fill_color='PuRd',
            fill_opacity=0.7,
            line_opacity=1,
            legend_name='Total Amount (Millionchf)',
            topojson='objects.cantons')
m.save('cantons_map.html')
m

In [22]:
from IPython.display import Image
Image(filename='cantons_map.png')

N.B: The scale is in Millions of CHF 

N.B: We don't know how to add the caption to the map

# Bonus Question 

We decided to cut the map as follow (our choice is arbitrary):
the French part includes Genève, Vaud, Valais, Fribourg, Neuchatel and the Valais. Even if the Valais is half German speaker we found only one institution/university in the german side (FFHS) according to P3, so we decided to included in the French part. 
The Italian part includes only Tessin.
The rest of the cantons belongs to the German part.
Note that Jura is empty in our results.

In [14]:
frenchcantons = pd.Series(['Vaud', 'Valais/Wallis', 'Fribourg', 'Neuchâtel', 'Genève', 'Jura'])
French_cantons = Finale.loc[Finale['Canton'].isin(frenchcantons) ]
Italian_cantons = Finale.loc[Finale['Canton'] == 'Ticino']
German_cantons = Finale.ix[~(Finale['Canton'].isin(frenchcantons))]
German_cantons = German_cantons.ix[~(Finale['Canton']=='Ticino')]

In [15]:
Language_partition = pd.DataFrame(columns = [['Regions','Amount']])
dic1 = {'Regions' : 'French part' , 'Amount' : French_cantons['Approved Amount'].sum()}

dic2 = {'Regions' : 'German part' , 'Amount' : German_cantons['Approved Amount'].sum()}

dic3 = {'Regions' : 'Italian part' , 'Amount' : Italian_cantons['Approved Amount'].sum()}

Language_partition.append([pd.Series(dic1),pd.Series(dic2),pd.Series(dic3)], ignore_index=True)



Regions       Amount
0   French part  5270.637624
1   German part  6841.539810
2  Italian part   112.075035